# model TPH

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from datetime import timedelta
import re
from dateutil.parser import parse
import string
import warnings
warnings.filterwarnings('ignore')
import plotly.graph_objects as go
import missingno as msno
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import scipy
import researchpy as rp
from matplotlib.offsetbox import AnchoredText
import pacmap
from sklearn.compose import ColumnTransformer
from sklearn.cluster import KMeans
from sklearn.pipeline import Pipeline
import plotly.express as px
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from imblearn.over_sampling import RandomOverSampler
from sklearn.model_selection import train_test_split 
# Import Halving Grid Search
from sklearn.experimental import enable_halving_search_cv 
from sklearn.model_selection import HalvingGridSearchCV
import xgboost as xgb
from scipy.stats import kurtosis,skew
from numpy import mean,sqrt,square
from scipy.fftpack import fft, fftfreq
from sklearn.metrics import mean_squared_error
sns.set_style("darkgrid")
pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 100

In [3]:
# Función que filtra tags por alta correlación
def corrkill(dataframe, features, corr_cut=0.8):

    df = dataframe[features]
    dfcorr = pd.DataFrame(np.triu(df.corr()), columns=df.columns, index=df.columns)
    dfcorr = dfcorr.stack().reset_index()
    dfcorr.columns = ['Feat1','Feat2','Val']
    dfcorr = dfcorr[~dfcorr['Val'].isin([0,1])]
    dfcorr = dfcorr[dfcorr['Val'].abs()>corr_cut]
    dfcorr["Val"]=dfcorr["Val"].abs()
    
    return list(dfcorr['Feat2']), dfcorr.sort_values(by="Val",ascending=False)

In [4]:
variables_interes=['pyrite law', 'chalcopyrite law',
       'chalcocite law', 'covelin law', 'crusher index', 'sag power index',
       'ball work index', 'bornite law','charge cell', 'TPH','water', 'speed','HH TPH', 'granulometry', 'Edad','loss of TPH']
variables_interes

['pyrite law',
 'chalcopyrite law',
 'chalcocite law',
 'covelin law',
 'crusher index',
 'sag power index',
 'ball work index',
 'bornite law',
 'charge cell',
 'TPH',
 'water',
 'speed',
 'HH TPH',
 'granulometry',
 'Edad',
 'loss of TPH']

In [5]:
# read df full csv
df_full=pd.read_csv('../../data/consolidated data/df_full_01November2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')[variables_interes]["2020":"2021"]
df_full

pyrite law  chalcopyrite law  chalcocite law  \
Timestamp                                                           
2020-01-10 04:05:00        2.30              1.76            0.50   
2020-01-10 04:06:00        2.30              1.76            0.50   
2020-01-10 04:07:00        2.30              1.76            0.50   
2020-01-10 04:08:00        2.30              1.76            0.50   
2020-01-10 04:09:00        2.30              1.76            0.50   
...                         ...               ...             ...   
2021-12-31 23:55:00        1.87              0.81            0.35   
2021-12-31 23:56:00        1.87              0.81            0.35   
2021-12-31 23:57:00        1.87              0.81            0.35   
2021-12-31 23:58:00        1.87              0.81            0.35   
2021-12-31 23:59:00        1.87              0.81            0.35   

                     covelin law  crusher index  sag power index  \
Timestamp                                                          
2020-01-10 04:05:00         0.02        19.7649          98.5569   
2020-01-10 04:06:00         0.02        19.7649          98.5569   
2020-01-10 04:07:00         0.02        19.7649          98.5569   
2020-01-10 04:08:00         0.02        19.7649          98.5569   
2020-01-10 04:09:00         0.02        19.7649          98.5569   
...                          ...            ...              ...   
2021-12-31 23:55:00         0.02        22.7872         107.8278   
2021-12-31 23:56:00         0.02        22.7872         107.8278   
2021-12-31 23:57:00         0.02        22.7872         107.8278   
2021-12-31 23:58:00         0.02        22.7872         107.8278   
2021-12-31 23:59:00         0.02        22.7872         107.8278   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2020-01-10 04:05:00          15.4504         0.05   809.237330  4317.030837   
2020-01-10 04:06:00          15.4504         0.05   808.519162  4053.372184   
2020-01-10 04:07:00          15.4504         0.05   803.154714  4087.871015   
2020-01-10 04:08:00          15.4504         0.05   800.856144  3995.961643   
2020-01-10 04:09:00          15.4504         0.05   798.234539  4019.595784   
...                              ...          ...          ...          ...   
2021-12-31 23:55:00          15.9269         0.01   660.131439  3999.947365   
2021-12-31 23:56:00          15.9269         0.01   659.925303  4009.511846   
2021-12-31 23:57:00          15.9269         0.01   660.528146  3986.674246   
2021-12-31 23:58:00          15.9269         0.01   662.163283  3987.205474   
2021-12-31 23:59:00          15.9269         0.01   664.242088  3972.307885   

                           water     speed  HH TPH  granulometry  Edad  \
Timestamp                                                                
2020-01-10 04:05:00  1539.203093  9.063024  3950.0     48.829422   1.0   
2020-01-10 04:06:00  1488.284682  9.062035  3950.0     48.633147   1.0   
2020-01-10 04:07:00  1484.665416  9.063110  3950.0     48.493040   1.0   
2020-01-10 04:08:00  1461.269967  9.017207  3950.0     48.465917   1.0   
2020-01-10 04:09:00  1443.665449  9.000981  3950.0     48.495837   1.0   
...                          ...       ...     ...           ...   ...   
2021-12-31 23:55:00  1320.091670  8.108425  4000.0     72.978907   2.0   
2021-12-31 23:56:00  1279.398901  8.102690  4000.0     73.121518   2.0   
2021-12-31 23:57:00  1249.692430  8.098562  4000.0     73.399275   2.0   
2021-12-31 23:58:00  1228.624741  8.097747  4000.0     73.050212   2.0   
2021-12-31 23:59:00  1209.035456  8.095141  4000.0     72.604623   2.0   

                     loss of TPH  
Timestamp                         
2020-01-10 04:05:00            0  
2020-01-10 04:06:00            0  
2020-01-10 04:07:00            0  
2020-01-10 04:08:00            0  
2020-01-10 04:09:00            0  
..

In [ ]:
df_corr = df_full.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))
top_corr=corr_tph[corr_tph.TPH>=0]
top_corr

# Feature Engineering

In [ ]:
def feature_engineering(df):
      
    targets = ["TPH","Edad","loss of TPH","HH TPH"]
    df_vars = df.copy()
    column_inicial=df_vars.columns

    for column in df_vars:
    
        if (column not in targets):

            ## 10 min
            df_vars[f"skew_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:skew(x))
            df_vars[f"kurt_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: np.nanvar(x))

            # 5 min
            df_vars[f"mean_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: np.nanvar(x))

            # 3 min
            df_vars[f"skew_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:skew(x))
            df_vars[f"kurt_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmax(list(x)))
            df_vars[f"sum_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: np.nanvar(x))

            # Fourier
            #L=10
            #df_vars[f"fourier_{L}_max_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmax(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_min_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmin(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_mean_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmean(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_sum_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nansum(abs(fft(list(x))[1:int(L/2)]/(L/2))))
#
            #L=5
            #df_vars[f"fourier_{L}_max_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmax(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_min_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmin(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_mean_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nanmean(abs(fft(list(x))[1:int(L/2)]/(L/2))))
            #df_vars[f"fourier_{L}_sum_{column}"]=df_vars[column].rolling(window=L).apply(lambda x:    np.nansum(abs(fft(list(x))[1:int(L/2)]/(L/2))))


    for column in column_inicial:
        if (column not in targets):
            # lags  
            df_vars[f"{column}_(t-1)"] = df_vars[column].shift(1)
            df_vars[f'{column}_(t-2)'] = df_vars[column].shift(2)
            df_vars[f'{column}_(t-3)'] = df_vars[column].shift(3)
            df_vars[f'{column}_(t-4)'] = df_vars[column].shift(4)
            df_vars[f'{column}_(t-5)'] = df_vars[column].shift(5)
           
    
    return df_vars
   

In [ ]:
df_features=feature_engineering(df_full)

In [ ]:
# Se guarda en csv
df_features.to_csv('../../data/consolidated data/df_features_'+pd.to_datetime('today').strftime('%d%B%Y')+'.csv', index=True)

In [7]:
# read df full csv
df_features=pd.read_csv('../../data/consolidated data/df_features_05November2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')["2020":"2021"]
df_features["TPH"]=df_features["TPH"].shift(-15)
df_features["loss of TPH"]=df_features["loss of TPH"].shift(-15)
df_features.dropna(inplace=True)
df_features.sort_index(inplace=True)
df_features.shape

(796462, 340)

# Correlación entre variables

In [8]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(df_features,df_features.columns)

In [9]:
# Tags altamente correlacionados
table_cor

Feat1                    Feat2       Val
83206             mean_speed_5              sum_speed_5  1.000000
38194     mean_crusher index_5      sum_crusher index_5  1.000000
28646      mean_covelin law_10       sum_covelin law_10  1.000000
30692       mean_covelin law_5        sum_covelin law_5  1.000000
88662     mean_granulometry_10      sum_granulometry_10  1.000000
...                        ...                      ...       ...
10593        kurt_pyrite law_3  kurt_chalcopyrite law_3  0.842415
25619    kurt_chalcocite law_3     kurt_crusher index_3  0.838370
18139  kurt_chalcopyrite law_3     kurt_crusher index_3  0.836664
10615        kurt_pyrite law_3    kurt_chalcocite law_3  0.821204
10659        kurt_pyrite law_3     kurt_crusher index_3  0.803003

[2550 rows x 3 columns]

In [10]:
df_corr = df_features.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))


In [11]:
top_corr=corr_tph[corr_tph.TPH>=0.15]
top_corr

TPH
TPH                     1.000000
HH TPH                  0.619719
loss of TPH             0.556349
max_sag power index_10  0.250927
rms_sag power index_10  0.250926
...                          ...
min_water_10            0.164453
min_water_5             0.158340
kurt_water_3            0.156106
min_water_3             0.155370
water                   0.151874

[92 rows x 1 columns]

# Equilibrio de eventos de perdidas de TPH

In [12]:
# Generación de targets ficticio y features
target=df_features["2020":"2021-11"]["loss of TPH"].copy()
features=df_features["2020":"2021-11"].drop(columns=["loss of TPH"])

# Generación conjunto de train y test 
Xtrain, Xtest, Ytrain, Ytest = train_test_split(
    features, target, test_size=0.33, 
    random_state=42
)

# Sobremuestreo: Aumentar numero de datos de la clase minoritaria (perdida de TPH)
# ROS(Duplica clases):
ros=RandomOverSampler(random_state=0) # Random_state=0

# ROS:
Xtrain, Ytrain=ros.fit_resample(Xtrain,Ytrain)

In [13]:
Color_loss=Ytest
Color_loss=Color_loss.astype(str)

In [14]:
# Ytest reg
Ytest=Xtest["TPH"]
Xtest=Xtest.drop(columns=["TPH"])

In [15]:
# Ytrain reg
Ytrain=Xtrain["TPH"]
Xtrain=Xtrain.drop(columns=["TPH"])

# Feature selection

In [ ]:
# Generación de targets ficticio y features
#target=df_features["2020":"2021-11"]["TPH"].copy()
#features=df_features["2020":"2021-11"].drop(columns=["loss of TPH","TPH"])
#
## Generación conjunto de train y test 
#Xtrain, Xtest, Ytrain, Ytest = train_test_split(
#    features, target, test_size=0.33, 
#    random_state=42
#)

In [16]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        Xtrain.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [17]:
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['pyrite law',
                                                   'chalcopyrite law',
                                                   'chalcocite law',
                                                   'covelin law',
                                                   'crusher index',
                                                   'sag power index',
                                                   'ball work index',
                                                   'bornite law', 'charge cell',
                                                   'water', 'speed', 'HH TPH',
                                                   'granulometry', 'Edad',
                                                   'skew_pyrite law_10',
                                                   'kurt_pyrite law_10',
                           

In [18]:
Ypred= pipe.predict(Xtest)

# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.8021847116764176 
 RMSE:  200.94186540116752


In [19]:
# test 2021
test_time_serie=df_features["2021-12"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)
#test_time_serie["TPH predict"]=test_time_serie["TPH predict"].shift(5)
test_time_serie.dropna(inplace=True)

# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))

R2:  0.6834317491282671 
 RMSE:  198.74315497251507


In [20]:
df_importance=pd.DataFrame({"tag":Xtrain.columns,"importance":pipe["clf"].feature_importances_}).sort_values(by="importance",ascending=False).reset_index(drop=True)
df_importance.head()

tag  importance
0              HH TPH    0.067485
1               water    0.042324
2   min_charge cell_3    0.032941
3         max_water_3    0.029797
4  mean_charge cell_3    0.016593

In [21]:
pd.options.plotting.backend = "plotly"
fig=df_importance["importance"].plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [22]:
# Plot
fig = go.Figure([go.Bar(x=df_importance["tag"], y=df_importance["importance"])])
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [23]:
xgboost_fs=df_importance[:100].tag.to_list()
xgboost_fs

['HH TPH',
 'water',
 'min_charge cell_3',
 'max_water_3',
 'mean_charge cell_3',
 'min_water_5',
 'max_charge cell_10',
 'min_speed_10',
 'mean_ball work index_5',
 'max_speed_10',
 'max_water_10',
 'min_charge cell_10',
 'max_sag power index_10',
 'mean_chalcocite law_5',
 'max_pyrite law_5',
 'rms_covelin law_5',
 'min_granulometry_10',
 'ball work index_(t-4)',
 'min_covelin law_3',
 'min_speed_5',
 'max_bornite law_10',
 'var_water_10',
 'Edad',
 'rms_speed_10',
 'min_water_10',
 'rms_granulometry_10',
 'rms_chalcocite law_5',
 'min_sag power index_5',
 'var_bornite law_3',
 'sag power index',
 'mean_chalcocite law_10',
 'min_pyrite law_10',
 'chalcocite law_(t-2)',
 'max_pyrite law_3',
 'min_ball work index_10',
 'max_crusher index_5',
 'charge cell',
 'rms_sag power index_10',
 'min_chalcopyrite law_10',
 'speed_(t-3)',
 'max_crusher index_10',
 'crusher index_(t-5)',
 'min_bornite law_3',
 'min_sag power index_10',
 'rms_crusher index_10',
 'chalcocite law_(t-3)',
 'rms_chalcoc

In [24]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(Xtrain,xgboost_fs,corr_cut=0.9)

In [25]:
# Tags altamente correlacionados
table_cor

Feat1                  Feat2       Val
4860     mean_charge cell_10     rms_charge cell_10  0.999994
4486    rms_crusher index_10  mean_crusher index_10  0.999982
1326   mean_chalcocite law_5   rms_chalcocite law_5  0.999904
492       mean_charge cell_3      charge cell_(t-1)  0.999881
3046  mean_chalcocite law_10  rms_chalcocite law_10  0.999803
...                      ...                    ...       ...
973             max_speed_10            speed_(t-4)  0.948916
964             max_speed_10            rms_speed_3  0.947156
939             max_speed_10            speed_(t-3)  0.947018
1024            max_water_10           min_water_10  0.945102
919             max_speed_10            min_speed_5  0.920350

[329 rows x 3 columns]

In [26]:
tag_select = [i for i in xgboost_fs if i not in collinearity]
tag_select

['HH TPH',
 'water',
 'min_charge cell_3',
 'min_speed_10',
 'mean_ball work index_5',
 'max_speed_10',
 'max_sag power index_10',
 'mean_chalcocite law_5',
 'max_pyrite law_5',
 'rms_covelin law_5',
 'min_granulometry_10',
 'max_bornite law_10',
 'var_water_10',
 'Edad',
 'var_bornite law_3',
 'max_crusher index_5',
 'min_chalcopyrite law_10',
 'var_charge cell_10',
 'var_sag power index_10',
 'skew_bornite law_10',
 'var_water_3']

In [27]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [28]:
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['HH TPH', 'water',
                                                   'min_charge cell_3',
                                                   'min_speed_10',
                                                   'mean_ball work index_5',
                                                   'max_speed_10',
                                                   'max_sag power index_10',
                                                   'mean_chalcocite law_5',
                                                   'max_pyrite law_5',
                                                   'rms_covelin law_5',
                                                   'min_granulometry_10',
                                                   'max_bornite law_10',
                                                   'var_water_10', 'Edad',
                

In [29]:
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.8030912049917942 
 RMSE:  200.48092626363015


# GridSearch

In [30]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        #features.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
        #("Selection", SelectPercentile(f_classif, percentile=10)),
        #("PCA",PCA(n_components=150 )), #0.08
     ("reg", xgb.XGBRegressor(seed=1,eval_metric='rmse'))
    ]
)


param_grid_reg = {'reg__learning_rate': list(np.linspace(0.001,1,10)), # Boosting learning rate
                  'reg__gamma':list(np.linspace(0.0001,50,5)), # Minimum loss reduction required to make a further partition on a leaf node of the tree.
                  #'reg__max_depth':[5,10,12,15,20], # Maximum tree depth for base learners.
                  #'reg__min_child_weight':[10,5,1,2,3], # Minimum sum of instance weight(hessian) needed in a child.
                  #'reg__colsample_bytree':[0.5,0.8,1], # Subsample ratio of columns when constructing each tree.
                  'reg__n_estimators': [100,200,300], # Number of gradient boosted trees.   
                  #'reg__reg_alpha': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
              #'reg__reg_lambda': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
               #'Selection__percentile': [10,20,30,50,70,80,100]              
                 } 

# Clasificación
gs_reg = HalvingGridSearchCV(pipe, param_grid_reg, scoring='neg_mean_absolute_error',cv=5,refit=True,
                             verbose=10,
                             aggressive_elimination=True
                            )

# Fit
gs_reg.fit(Xtrain, Ytrain)

n_iterations: 5
n_required_iterations: 5
n_possible_iterations: 5
min_resources_: 8597
max_resources_: 696406
aggressive_elimination: True
factor: 3
----------
iter: 0
n_candidates: 150
n_resources: 8597
Fitting 5 folds for each of 150 candidates, totalling 750 fits
[CV 1/5; 1/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100
[CV 1/5; 1/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100;, score=(train=-3620.604, test=-3754.329) total time=   8.5s
[CV 2/5; 1/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100
[CV 2/5; 1/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100;, score=(train=-3628.488, test=-3746.164) total time=   0.7s
[CV 3/5; 1/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100
[CV 3/5; 1/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100;, score=(train=-3608.216, test=-3741.728) total time=   0.7s
[CV 4/5; 1/150] START 

HalvingGridSearchCV(aggressive_elimination=True,
                    estimator=Pipeline(steps=[('preprocesamiento',
                                               ColumnTransformer(transformers=[('MinMax',
                                                                                MinMaxScaler(),
                                                                                ['HH '
                                                                                 'TPH',
                                                                                 'water',
                                                                                 'min_charge '
                                                                                 'cell_3',
                                                                                 'min_speed_10',
                                                                                 'mean_ball '
                                                        

In [31]:
gs_reg.best_score_

-112.34613867079372

In [32]:
gs_reg.best_params_

{'reg__gamma': 12.500074999999999,
 'reg__learning_rate': 0.334,
 'reg__n_estimators': 300}

In [33]:
Ypred= gs_reg.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.869997378424901 
 RMSE:  162.89830224052227


# Train model

In [10]:
tag_select=['HH TPH',
 'water',
 'min_charge cell_3',
 'min_speed_10',
 'mean_ball work index_5',
 'max_speed_10',
 'max_sag power index_10',
 'mean_chalcocite law_5',
 'max_pyrite law_5',
 'rms_covelin law_5',
 'min_granulometry_10',
 'max_bornite law_10',
 'var_water_10',
 'Edad',
 'var_bornite law_3',
 'max_crusher index_5',
 'min_chalcopyrite law_10',
 'var_charge cell_10',
 'var_sag power index_10',
 'skew_bornite law_10',
 'var_water_3']

In [34]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse',gamma= 12.500074999999999, learning_rate= 0.334, n_estimators= 300
     
     ))
    ]
)
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['HH TPH', 'water',
                                                   'min_charge cell_3',
                                                   'min_speed_10',
                                                   'mean_ball work index_5',
                                                   'max_speed_10',
                                                   'max_sag power index_10',
                                                   'mean_chalcocite law_5',
                                                   'max_pyrite law_5',
                                                   'rms_covelin law_5',
                                                   'min_granulometry_10',
                                                   'max_bornite law_10',
                                                   'var_water_10', 'Edad',
                

In [35]:
from sklearn.metrics import mean_absolute_percentage_error

In [36]:
mean_absolute_percentage_error(Ytest, Ypred)*100

2.6396250215630657

In [37]:
# test 2020
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False),'\n','MAPE :',mean_absolute_percentage_error(Ytest, Ypred)*100)

R2:  0.869997378424901 
 RMSE:  162.89830224052227 
 MAPE : 2.6396250215630657


In [38]:
# Create traces
fig = px.scatter(x=Ypred[:10000], y=Ytest[:10000],trendline="ols",trendline_color_override="red",labels={'y': 'Test',"x":"Predict"},color=Color_loss[:10000])
fig.update_layout(height=500, width=1200, title_text="Scatter predict/test")
fig.show()

In [39]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(y=Ypred[:1000], 
                    mode='lines',name="predict"
                    ))

fig.add_trace(go.Scatter(y=Ytest[:1000],
                    mode='lines',name="Test",#marker=dict(color=list(Color_loss[:1000]))
                    ))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict")
fig.show()

# Simulation time series predict

In [40]:
# test 2021
test_time_serie=df_features["2021-12"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)
#test_time_serie["TPH predict"]=test_time_serie["TPH predict"].shift(5)
test_time_serie.dropna(inplace=True)

# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))

R2:  0.620929326576005 
 RMSE:  217.4796347164161


In [41]:
data=test_time_serie
data.head()

pyrite law  chalcopyrite law  chalcocite law  \
Timestamp                                                           
2021-12-01 00:00:00        2.04               1.0            0.29   
2021-12-01 00:01:00        2.04               1.0            0.29   
2021-12-01 00:02:00        2.04               1.0            0.29   
2021-12-01 00:03:00        2.04               1.0            0.29   
2021-12-01 00:04:00        2.04               1.0            0.29   

                     covelin law  crusher index  sag power index  \
Timestamp                                                          
2021-12-01 00:00:00         0.02        19.9309           118.08   
2021-12-01 00:01:00         0.02        19.9309           118.08   
2021-12-01 00:02:00         0.02        19.9309           118.08   
2021-12-01 00:03:00         0.02        19.9309           118.08   
2021-12-01 00:04:00         0.02        19.9309           118.08   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2021-12-01 00:00:00          16.3835         0.01   768.741664  3948.391833   
2021-12-01 00:01:00          16.3835         0.01   769.288545  4065.365564   
2021-12-01 00:02:00          16.3835         0.01   769.324759  4120.824132   
2021-12-01 00:03:00          16.3835         0.01   771.590130  4161.911848   
2021-12-01 00:04:00          16.3835         0.01   772.882214  4146.338961   

                           water     speed  HH TPH  granulometry  Edad  \
Timestamp                                                                
2021-12-01 00:00:00  2036.974410  9.295474  4200.0     53.602944   2.0   
2021-12-01 00:01:00  2040.755290  9.294131  4200.0     53.646366   2.0   
2021-12-01 00:02:00  2039.094777  9.294869  4200.0     53.563687   2.0   
2021-12-01 00:03:00  2037.114180  9.298192  4200.0     53.712367   2.0   
2021-12-01 00:04:00  2040.755205  9.297221  4200.0     53.944855   2.0   

                     loss of TPH  skew_pyrite law_10  kurt_pyrite law_10  \
Timestamp                                                                  
2021-12-01 00:00:00          1.0       -2.666667e+00            5.111111   
2021-12-01 00:01:00          1.0       -1.500000e+00            0.250000   
2021-12-01 00:02:00          1.0       -8.728716e-01           -1.238095   
2021-12-01 00:03:00          1.0       -4.082483e-01           -1.833333   
2021-12-01 00:04:00          1.0        7.436229e-15           -2.000000   

                     mean_pyrite law_10  max_pyrite law_10  sum_pyrite law_10  \
Timestamp                                                                       
2021-12-01 00:00:00               2.202               2.22              22.02   
2021-12-01 00:01:00               2.184               2.22              21.84   
2021-12-01 00:02:00               2.166               2.22              21.66   
2021-12-01 00:03:00               2.148               2.22              21.48   
2021-12-01 00:04:00               2.130               2.22              21.30   

                     min_pyrite law_10  rms_pyrite law_10  var_pyrite law_10  \
Timestamp                                                                      
2021-12-01 00:00:00               2.04           2.202662           0.002916   
2021-12-01 00:01:00               2.04           2.185186           0.005184   
2021-12-01 00:02:00               2.04           2.167570           0.006804   
2021-12-01 00:03:00               2.04           2.149809           0.007776   
2021-12-01 00:04:00               2.04           2.131901           0.008100   

                     mean_pyrite law_5  max_pyrite law_5  sum_pyrite law_5  \
Timestamp                                                                    
2021-12-01 00:00:00              2.184              2.22             10.92   
2021-12-01 00:01:00              2.148              2.22             10.74   
2021-12-01 00

In [42]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

#fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
#                    mode='lines',
#                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()

In [36]:
fig.write_html("file.html")